 # Dual Moving Average Crossover Trading Signal

 ---

 ### Import Libraries and Dependencies

In [1]:
# Import libraries and dependencies
import numpy as np
import pandas as pd
import hvplot
import hvplot.pandas
from pathlib import Path
import plotly.express as px
import panel as pn

pn.extension()

pd.set_option("display.max_rows", 2000)
pd.set_option("display.max_columns", 2000)
pd.set_option("display.width", 1000)

 ### Read CSV into Pandas DataFrame

In [2]:
# Set the file path
filepath = Path("../Resources/aapl.csv")

# Read the CSV located at the file path into a Pandas DataFrame
# Set the `Date` column as the index and auto-format the datetime string
aapl_df = pd.read_csv(filepath, parse_dates=True, infer_datetime_format=True)

# Print the DataFrame
aapl_df.head()

date   close    volume    open    high     low
0  9/22/14  101.06  52421660  101.80  102.14  100.58
1  9/23/14  102.64  63255860  100.60  102.94  100.54
2  9/24/14  101.75  59974260  102.16  102.85  101.20
3  9/25/14   97.87  99689300  100.51  100.71   97.72
4  9/26/14  100.75  62276770   98.53  100.75   98.40

 ### Generate a Dual Moving Average Crossover Trading Signal

In [3]:
# Grab just the `date` and `close` from the dataset
signals_df = aapl_df.loc[:, ["date", "close"]].copy()

# Set the short window and long windows
short_window = 50
long_window = 100

# Set the `date` column as the index
signals_df = signals_df.set_index("date", drop=True)

# Generate the short and long moving averages (50 and 100 days, respectively)
signals_df["SMA50"] = signals_df["close"].rolling(window=short_window).mean()
signals_df["SMA100"] = signals_df["close"].rolling(window=long_window).mean()
signals_df["Signal"] = 0.0

# Generate the trading signal 0 or 1,
# where 0 is when the SMA50 is under the SMA100, and
# where 1 is when the SMA50 is higher (or crosses over) the SMA100
signals_df["Signal"][short_window:] = np.where(
    signals_df["SMA50"][short_window:] > signals_df["SMA100"][short_window:], 1.0, 0.0
)

# Calculate the points in time at which a position should be taken, 1 or -1
signals_df["Entry/Exit"] = signals_df["Signal"].diff()

signals_df.tail()

close     SMA50     SMA100  Signal  Entry/Exit
date                                                    
9/13/19  218.75  207.0573  200.50975     1.0         0.0
9/16/19  219.90  207.3707  200.63715     1.0         0.0
9/17/19  220.70  207.7843  200.79135     1.0         0.0
9/18/19  222.77  208.2149  200.97605     1.0         0.0
9/19/19  220.96  208.5695  201.13955     1.0         0.0

 ### Plot Entry and Exit Points of Dual Moving Average Crossover Trading Strategy

In [4]:
# Visualize exit position relative to close price
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['close'].hvplot.scatter(
    color='red',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize entry position relative to close price
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['close'].hvplot.scatter(
    color='green',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = signals_df[['close']].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs = signals_df[['SMA50', 'SMA100']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I          :Curve   [date]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .Scatter.Close.I  :Scatter   [date]   (close)
   .Scatter.Close.II :Scatter   [date]   (close)

In [5]:
# Set initial capital
initial_capital = float(100000)

# Set the share size
share_size = 500

# Take a 500 share position where the dual moving average crossover is 1 (SMA50 is greater than SMA100)
signals_df['Position'] = share_size * signals_df['Signal']

# Find the points in time where a 500 share position is bought or sold
signals_df['Entry/Exit Position'] = signals_df['Position'].diff()

# Multiply share price by entry/exit positions and get the cumulatively sum
signals_df['Portfolio Holdings'] = signals_df['close'] * signals_df['Entry/Exit Position'].cumsum()

# Subtract the initial capital by the portfolio holdings to get the amount of liquid cash in the portfolio
signals_df['Portfolio Cash'] = initial_capital - (signals_df['close'] * signals_df['Entry/Exit Position']).cumsum()

# Get the total portfolio value by adding the cash amount by the portfolio holdings (or investments)
signals_df['Portfolio Total'] = signals_df['Portfolio Cash'] + signals_df['Portfolio Holdings']

# Calculate the portfolio daily returns
signals_df['Portfolio Daily Returns'] = signals_df['Portfolio Total'].pct_change()

# Calculate the cumulative returns
signals_df['Portfolio Cumulative Returns'] = (1 + signals_df['Portfolio Daily Returns']).cumprod() - 1

# Print the DataFrame
signals_df.tail(10)

close     SMA50     SMA100  Signal  Entry/Exit  Position  Entry/Exit Position  Portfolio Holdings  Portfolio Cash  Portfolio Total  Portfolio Daily Returns  Portfolio Cumulative Returns
date                                                                                                                                                                                                
9/6/19   213.260  205.2584  199.72930     1.0         0.0     500.0                  0.0            106630.0         22495.0         129125.0                -0.000077                      0.291250
9/9/19   214.170  205.5470  199.87850     1.0         0.0     500.0                  0.0            107085.0         22495.0         129580.0                 0.003524                      0.295800
9/10/19  216.700  205.9226  200.01420     1.0         0.0     500.0                  0.0            108350.0         22495.0         130845.0                 0.009762                      0.308450
9/11/19  223.590  206.3634  200.21150     1.0         0.0     500.0                  0.0            111795.0         22495.0         134290.0                 0.026329                      0.342900
9/12/19  223.085  206.7705  200.39705     1.0         0.0     500.0                  0.0            111542.5         22495.0         134037.5                -0.001880                      0.340375
9/13/19  218.750  207.0573  200.50975     1.0         0.0     500.0                  0.0            109375.0         22495.0         131870.0                -0.016171                      0.318700
9/16/19  219.900  207.3707  200.63715     1.0         0.0     500.0                  0.0            109950.0         22495.0         132445.0                 0.004360                      0.324450
9/17/19  220.700  207.7843  200.79135     1.0         0.0     500.0                  0.0            110350.0         22495.0         132845.0                 0.003020                      0.328450
9/18/19  222.770  208.2149  200.97605     1.0         0.0     500.0                  0.0            111385.0         22495.0         133880.0                 0.007791                      0.338800
9/19/19  220.960  208.5695  201.13955     1.0         0.0     500.0                  0.0            110480.0         22495.0         132975.0                -0.006760                      0.329750

In [6]:
# Visualize exit position relative to total portfolio value
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Portfolio Total'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Portfolio Total'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize total portoflio value for the investment
total_portfolio_value = signals_df[['Portfolio Total']].hvplot(
    line_color='lightgray',
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Overlay plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I                    :Curve   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.I  :Scatter   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.II :Scatter   [date]   (Portfolio Total)

### 2/7 windows

In [7]:
# Grab just the `date` and `close` from the dataset
signals_df = aapl_df.loc[:, ["date", "close"]].copy()

# Set the short window and long windows
short_window = 2
long_window = 7

# Set the `date` column as the index
signals_df = signals_df.set_index("date", drop=True)

# Generate the short and long moving averages (50 and 100 days, respectively)
signals_df["SMA50"] = signals_df["close"].rolling(window=short_window).mean()
signals_df["SMA100"] = signals_df["close"].rolling(window=long_window).mean()
signals_df["Signal"] = 0.0

# Generate the trading signal 0 or 1,
# where 0 is when the SMA50 is under the SMA100, and
# where 1 is when the SMA50 is higher (or crosses over) the SMA100
signals_df["Signal"][short_window:] = np.where(
    signals_df["SMA50"][short_window:] > signals_df["SMA100"][short_window:], 1.0, 0.0
)

# Calculate the points in time at which a position should be taken, 1 or -1
signals_df["Entry/Exit"] = signals_df["Signal"].diff()

signals_df.tail()

close     SMA50      SMA100  Signal  Entry/Exit
date                                                     
9/13/19  218.75  220.9175  217.547857     1.0         0.0
9/16/19  219.90  219.3250  218.493571     1.0         0.0
9/17/19  220.70  220.3000  219.556429     1.0         0.0
9/18/19  222.77  221.7350  220.785000     1.0         0.0
9/19/19  220.96  221.8650  221.393571     1.0         0.0

In [8]:
# Visualize exit position relative to close price
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['close'].hvplot.scatter(
    color='red',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize entry position relative to close price
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['close'].hvplot.scatter(
    color='green',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = signals_df[['close']].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs = signals_df[['SMA50', 'SMA100']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I          :Curve   [date]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .Scatter.Close.I  :Scatter   [date]   (close)
   .Scatter.Close.II :Scatter   [date]   (close)

In [9]:
# Set initial capital
initial_capital = float(100000)

# Set the share size
share_size = 500

# Take a 500 share position where the dual moving average crossover is 1 (SMA50 is greater than SMA100)
signals_df['Position'] = share_size * signals_df['Signal']

# Find the points in time where a 500 share position is bought or sold
signals_df['Entry/Exit Position'] = signals_df['Position'].diff()

# Multiply share price by entry/exit positions and get the cumulatively sum
signals_df['Portfolio Holdings'] = signals_df['close'] * signals_df['Entry/Exit Position'].cumsum()

# Subtract the initial capital by the portfolio holdings to get the amount of liquid cash in the portfolio
signals_df['Portfolio Cash'] = initial_capital - (signals_df['close'] * signals_df['Entry/Exit Position']).cumsum()

# Get the total portfolio value by adding the cash amount by the portfolio holdings (or investments)
signals_df['Portfolio Total'] = signals_df['Portfolio Cash'] + signals_df['Portfolio Holdings']

# Calculate the portfolio daily returns
signals_df['Portfolio Daily Returns'] = signals_df['Portfolio Total'].pct_change()

# Calculate the cumulative returns
signals_df['Portfolio Cumulative Returns'] = (1 + signals_df['Portfolio Daily Returns']).cumprod() - 1

# Print the DataFrame
signals_df

close     SMA50      SMA100  Signal  Entry/Exit  Position  Entry/Exit Position  Portfolio Holdings  Portfolio Cash  Portfolio Total  Portfolio Daily Returns  Portfolio Cumulative Returns
date                                                                                                                                                                                                  
9/22/14   101.060       NaN         NaN     0.0         NaN       0.0                  NaN                 NaN             NaN              NaN                      NaN                           NaN
9/23/14   102.640  101.8500         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                      NaN                           NaN
9/24/14   101.750  102.1950         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/25/14    97.870   99.8100         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/26/14   100.750   99.3100         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/29/14   100.110  100.4300         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/30/14   100.750  100.4300  100.704286     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/1/14    99.180   99.9650  100.435714     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/2/14    99.900   99.5400  100.044286     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/3/14    99.620   99.7600   99.740000     1.0         1.0     500.0                500.0             49810.0         50190.0         100000.0                 0.000000                      0.000000
10/6/14    99.620   99.6200   99.990000     0.0        -1.0       0.0               -500.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/7/14    98.750   99.1850   99.704286     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/8/14   100.800   99.7750   99.802857     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/9/14   101.020  100.9100   99.841429     1.0         1.0     500.0                500.0             50510.0         49490.0         100000.0                 0.000000                      0.000000
10/10/14  100.730  100.8750  100.062857     1.0         0.0     500.0                  0.0             50365.0         49490.0          99855.0                -0.001450                     -0.001450
10/13/14   99.810  100.2700  100.050000     1.0         0.0     500.0                  0.0             49905.0         49490.0          99395.0                -0.004607                     -0.006050
10/14/14   98.750   99.2800   99.925714     0.0        -1.0       0.0               -500.0                 0.0         98865.0          98865.0                -0.005332                     -0.011350
10/15/14   97.540   98.1450   99.628571     0.0         0.0       0.0                  0.0                 0.0         98865.0          98865.0                 0.000000                     -0.011350
10/16/14   96.260   96.9000   99

In [10]:
# Visualize exit position relative to total portfolio value
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Portfolio Total'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Portfolio Total'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize total portoflio value for the investment
total_portfolio_value = signals_df[['Portfolio Total']].hvplot(
    line_color='lightgray',
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Overlay plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I                    :Curve   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.I  :Scatter   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.II :Scatter   [date]   (Portfolio Total)

### 2/6 windows

In [11]:
# Grab just the `date` and `close` from the dataset
signals_df = aapl_df.loc[:, ["date", "close"]].copy()

# Set the short window and long windows
short_window = 2
long_window = 6

# Set the `date` column as the index
signals_df = signals_df.set_index("date", drop=True)

# Generate the short and long moving averages (50 and 100 days, respectively)
signals_df["SMA50"] = signals_df["close"].rolling(window=short_window).mean()
signals_df["SMA100"] = signals_df["close"].rolling(window=long_window).mean()
signals_df["Signal"] = 0.0

# Generate the trading signal 0 or 1,
# where 0 is when the SMA50 is under the SMA100, and
# where 1 is when the SMA50 is higher (or crosses over) the SMA100
signals_df["Signal"][short_window:] = np.where(
    signals_df["SMA50"][short_window:] > signals_df["SMA100"][short_window:], 1.0, 0.0
)

# Calculate the points in time at which a position should be taken, 1 or -1
signals_df["Entry/Exit"] = signals_df["Signal"].diff()

signals_df.tail()

close     SMA50      SMA100  Signal  Entry/Exit
date                                                     
9/13/19  218.75  220.9175  218.259167     1.0         0.0
9/16/19  219.90  219.3250  219.365833     0.0        -1.0
9/17/19  220.70  220.3000  220.454167     0.0         0.0
9/18/19  222.77  221.7350  221.465833     1.0         1.0
9/19/19  220.96  221.8650  221.027500     1.0         0.0

In [12]:
# Visualize exit position relative to close price
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['close'].hvplot.scatter(
    color='red',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize entry position relative to close price
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['close'].hvplot.scatter(
    color='green',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = signals_df[['close']].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs = signals_df[['SMA50', 'SMA100']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I          :Curve   [date]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .Scatter.Close.I  :Scatter   [date]   (close)
   .Scatter.Close.II :Scatter   [date]   (close)

In [13]:
# Set initial capital
initial_capital = float(100000)

# Set the share size
share_size = 500

# Take a 500 share position where the dual moving average crossover is 1 (SMA50 is greater than SMA100)
signals_df['Position'] = share_size * signals_df['Signal']

# Find the points in time where a 500 share position is bought or sold
signals_df['Entry/Exit Position'] = signals_df['Position'].diff()

# Multiply share price by entry/exit positions and get the cumulatively sum
signals_df['Portfolio Holdings'] = signals_df['close'] * signals_df['Entry/Exit Position'].cumsum()

# Subtract the initial capital by the portfolio holdings to get the amount of liquid cash in the portfolio
signals_df['Portfolio Cash'] = initial_capital - (signals_df['close'] * signals_df['Entry/Exit Position']).cumsum()

# Get the total portfolio value by adding the cash amount by the portfolio holdings (or investments)
signals_df['Portfolio Total'] = signals_df['Portfolio Cash'] + signals_df['Portfolio Holdings']

# Calculate the portfolio daily returns
signals_df['Portfolio Daily Returns'] = signals_df['Portfolio Total'].pct_change()

# Calculate the cumulative returns
signals_df['Portfolio Cumulative Returns'] = (1 + signals_df['Portfolio Daily Returns']).cumprod() - 1

# Print the DataFrame
signals_df

close     SMA50      SMA100  Signal  Entry/Exit  Position  Entry/Exit Position  Portfolio Holdings  Portfolio Cash  Portfolio Total  Portfolio Daily Returns  Portfolio Cumulative Returns
date                                                                                                                                                                                                  
9/22/14   101.060       NaN         NaN     0.0         NaN       0.0                  NaN                 NaN             NaN              NaN                      NaN                           NaN
9/23/14   102.640  101.8500         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                      NaN                           NaN
9/24/14   101.750  102.1950         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/25/14    97.870   99.8100         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/26/14   100.750   99.3100         NaN     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/29/14   100.110  100.4300  100.696667     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
9/30/14   100.750  100.4300  100.645000     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/1/14    99.180   99.9650  100.068333     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/2/14    99.900   99.5400   99.760000     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/3/14    99.620   99.7600  100.051667     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/6/14    99.620   99.6200   99.863333     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/7/14    98.750   99.1850   99.636667     0.0         0.0       0.0                  0.0                 0.0        100000.0         100000.0                 0.000000                      0.000000
10/8/14   100.800   99.7750   99.645000     1.0         1.0     500.0                500.0             50400.0         49600.0         100000.0                 0.000000                      0.000000
10/9/14   101.020  100.9100   99.951667     1.0         0.0     500.0                  0.0             50510.0         49600.0         100110.0                 0.001100                      0.001100
10/10/14  100.730  100.8750  100.090000     1.0         0.0     500.0                  0.0             50365.0         49600.0          99965.0                -0.001448                     -0.000350
10/13/14   99.810  100.2700  100.121667     1.0         0.0     500.0                  0.0             49905.0         49600.0          99505.0                -0.004602                     -0.004950
10/14/14   98.750   99.2800   99.976667     0.0        -1.0       0.0               -500.0                 0.0         98975.0          98975.0                -0.005326                     -0.010250
10/15/14   97.540   98.1450   99.775000     0.0         0.0       0.0                  0.0                 0.0         98975.0          98975.0                 0.000000                     -0.010250
10/16/14   96.260   96.9000   99

In [14]:
# Visualize exit position relative to total portfolio value
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Portfolio Total'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Portfolio Total'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize total portoflio value for the investment
total_portfolio_value = signals_df[['Portfolio Total']].hvplot(
    line_color='lightgray',
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Overlay plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I                    :Curve   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.I  :Scatter   [date]   (Portfolio Total)
   .Scatter.Portfolio_Total.II :Scatter   [date]   (Portfolio Total)

In [15]:
# Prepare DataFrame for metrics
metrics = [
    'Annual Return',
    'Cumulative Returns',
    'Annual Volatility',
    'Sharpe Ratio',
    'Sortino Ratio']

columns = ['Backtest']

# Initialize the DataFrame with index set to evaluation metrics and column as `Backtest` (just like PyFolio)
portfolio_evaluation_df = pd.DataFrame(index=metrics, columns=columns)
portfolio_evaluation_df

Backtest
Annual Return           NaN
Cumulative Returns      NaN
Annual Volatility       NaN
Sharpe Ratio            NaN
Sortino Ratio           NaN

In [16]:
# Calculate cumulative return
portfolio_evaluation_df.loc['Cumulative Returns'] = signals_df['Portfolio Cumulative Returns'][-1]

# Calculate annualized return
portfolio_evaluation_df.loc['Annual Return'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252
)

# Calculate annual volatility
portfolio_evaluation_df.loc['Annual Volatility'] = (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)

# Calculate Sharpe Ratio
portfolio_evaluation_df.loc['Sharpe Ratio'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252) / (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)

# Calculate Downside Return
sortino_ratio_df = signals_df[['Portfolio Daily Returns']].copy()
sortino_ratio_df.loc[:,'Downside Returns'] = 0

target = 0
mask = sortino_ratio_df['Portfolio Daily Returns'] < target
sortino_ratio_df.loc[mask, 'Downside Returns'] = sortino_ratio_df['Portfolio Daily Returns']**2
portfolio_evaluation_df

# Calculate Sortino Ratio
down_stdev = np.sqrt(sortino_ratio_df['Downside Returns'].mean()) * np.sqrt(252)
expected_return = sortino_ratio_df['Portfolio Daily Returns'].mean() * 252
sortino_ratio = expected_return/down_stdev

portfolio_evaluation_df.loc['Sortino Ratio'] = sortino_ratio
portfolio_evaluation_df.head()

Backtest
Annual Return       0.084623
Cumulative Returns    0.4854
Annual Volatility   0.102044
Sharpe Ratio        0.829276
Sortino Ratio        1.15653

In [17]:
# Initialize trade evaluation DataFrame with columns
trade_evaluation_df = pd.DataFrame(
    columns=[
        'Stock', 
        'Entry Date', 
        'Exit Date', 
        'Shares', 
        'Entry Share Price', 
        'Exit Share Price', 
        'Entry Portfolio Holding', 
        'Exit Portfolio Holding', 
        'Profit/Loss']
)

trade_evaluation_df

Empty DataFrame
Columns: [Stock, Entry Date, Exit Date, Shares, Entry Share Price, Exit Share Price, Entry Portfolio Holding, Exit Portfolio Holding, Profit/Loss]
Index: []

In [18]:
# Initialize iterative variables
entry_date = ''
exit_date = ''
entry_portfolio_holding = 0
exit_portfolio_holding = 0
share_size = 0
entry_share_price = 0
exit_share_price = 0

# Loop through signal DataFrame
# If `Entry/Exit` is 1, set entry trade metrics
# Else if `Entry/Exit` is -1, set exit trade metrics and calculate profit,
# Then append the record to the trade evaluation DataFrame
for index, row in signals_df.iterrows():
    if row['Entry/Exit'] == 1:
        entry_date = index
        entry_portfolio_holding = abs(row['Portfolio Holdings'])
        share_size = row['Entry/Exit Position']
        entry_share_price = row['close']

    elif row['Entry/Exit'] == -1:
        exit_date = index
        exit_portfolio_holding = abs(row['close'] * row['Entry/Exit Position'])
        exit_share_price = row['close']
        profit_loss =  entry_portfolio_holding - exit_portfolio_holding
        trade_evaluation_df = trade_evaluation_df.append(
            {
                'Stock': 'AAPL',
                'Entry Date': entry_date,
                'Exit Date': exit_date,
                'Shares': share_size,
                'Entry Share Price': entry_share_price,
                'Exit Share Price': exit_share_price,
                'Entry Portfolio Holding': entry_portfolio_holding,
                'Exit Portfolio Holding': exit_portfolio_holding,
                'Profit/Loss': profit_loss
            },
            ignore_index=True)

# Print the DataFrame
trade_evaluation_df

Stock Entry Date Exit Date  Shares  Entry Share Price  Exit Share Price  Entry Portfolio Holding  Exit Portfolio Holding  Profit/Loss
0    AAPL    10/8/14  10/14/14   500.0             100.80            98.750                  50400.0                 49375.0       1025.0
1    AAPL   10/20/14   12/1/14   500.0              99.76           115.070                  49880.0                 57535.0      -7655.0
2    AAPL   12/18/14  12/31/14   500.0             112.65           110.380                  56325.0                 55190.0       1135.0
3    AAPL     1/8/15   1/14/15   500.0             111.89           109.800                  55945.0                 54900.0       1045.0
4    AAPL    1/21/15   2/26/15   500.0             109.55           130.415                  54775.0                 65207.5     -10432.5
5    AAPL    3/17/15   3/23/15   500.0             127.04           127.210                  63520.0                 63605.0        -85.0
6    AAPL    3/31/15   4/16/15   500.0             124.43           126.170                  62215.0                 63085.0       -870.0
7    AAPL    4/21/15   4/29/15   500.0             126.91           128.640                  63455.0                 64320.0       -865.0
8    AAPL    5/11/15   5/13/15   500.0             126.32           126.010                  63160.0                 63005.0        155.0
9    AAPL    5/14/15   5/27/15   500.0             128.95           132.045                  64475.0                 66022.5      -1547.5
10   AAPL    5/28/15   5/29/15   500.0             131.78           130.280                  65890.0                 65140.0        750.0
11   AAPL    6/11/15   6/12/15   500.0             128.59           127.170                  64295.0                 63585.0        710.0
12   AAPL    6/18/15   6/19/15   500.0             127.88           126.600                  63940.0                 63300.0        640.0
13   AAPL    6/24/15   6/26/15   500.0             128.11           126.750                  64055.0                 63375.0        680.0
14   AAPL     7/2/15    7/8/15   500.0             126.44           122.570                  63220.0                 61285.0       1935.0
15   AAPL    7/13/15   7/22/15   500.0             125.66           125.220                  62830.0                 62610.0        220.0
16   AAPL    8/10/15   8/12/15   500.0             119.72           115.240                  59860.0                 57620.0       2240.0
17   AAPL    8/17/15   8/19/15   500.0             117.16           115.010                  58580.0                 57505.0       1075.0
18   AAPL    8/27/15    9/2/15   500.0             112.92           112.340                  56460.0                 56170.0        290.0
19   AAPL     9/9/15   9/18/15   500.0             110.15           113.450                  55075.0                 56725.0      -1650.0
20   AAPL    9/24/15   9/28/15   500.0             115.00           112.440                  57500.0                 56220.0       1280.0
21   AAPL    10/5/15   10/8/15   500.0             110.78           109.500                  55390.0                 54750.0        640.0
22   AAPL   10/12/15  10/15/15   500.0             111.60           111.860                  55800.0                 55930.0       -130.0
23   AAPL   10/16/15  10/27/15   500.0             111.04           114.550                  55520.0                 57275.0      -1755.0
24   AAPL   10/28/15   11/6/15   500.0             119.27           121.060                  59635.0                 60530.0       -895.0
25   AAPL   11/18/15  11/27/15   500.0             117.29           117.810                  58645.0                 58905.0       -260.0
26   AAPL    12/7/15   12/9/15   500.0             118.28           115.620                  59140.0                 57810.0       1330.0
27   AAPL   12/24/15  12/29/15   500.0             108.03           108.740                  54015.0                 54370.0       -355.0
28

In [19]:
price_df = signals_df[['close', 'SMA50', 'SMA100']]
price_chart = price_df.hvplot.line()
price_chart.opts(xaxis=None)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [20]:
portfolio_evaluation_df.reset_index(inplace=True)
portfolio_evaluation_table = portfolio_evaluation_df.hvplot.table()
portfolio_evaluation_table

:Table   [index,Backtest]

In [21]:
trade_evaluation_table = trade_evaluation_df.hvplot.table()
trade_evaluation_table

:Table   [Stock,Entry Date,Exit Date,Shares,Entry Share Price,Exit Share Price,Entry Portfolio Holding,Exit Portfolio Holding,Profit/Loss]

In [22]:
# Create rows
price_chart_row = pn.Row(price_chart)
portfolio_evaluation_row = pn.Row(portfolio_evaluation_table)
trade_evaluation_row = pn.Row(trade_evaluation_table)

# Create columns
portfolio_column = pn.Column('# Portfolio Evaluation Metrics', price_chart_row, portfolio_evaluation_row)
trade_column = pn.Column('# Trade Evaluation Metrics', trade_evaluation_row)

# Create tabs
trading_dashboard = pn.Tabs(
    ("Portfolio Metrics", portfolio_column),
    ("Trade Metrics", trade_column)
)

In [23]:
trading_dashboard.servable()

Tabs
    [0] Column
        [0] Markdown(str)
        [1] Row
            [0] HoloViews(NdOverlay)
        [2] Row
            [0] HoloViews(Table)
    [1] Column
        [0] Markdown(str)
        [1] Row
            [0] HoloViews(Table)